<a href="https://colab.research.google.com/github/sunnygong369/Covisitation-Matrix/blob/main/MOVIE_MATRIX_COMPLETE.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### **Settings**

In [212]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


*   **Unpacking the zip to df**
(time: 15s)

**Data source:** https://www.kaggle.com/datasets/rounakbanik/the-movies-dataset?select=ratings.csv



In [213]:
import zipfile
import pandas as pd

df_zip = zipfile.ZipFile('/content/drive/MyDrive/Colab Notebooks/ratings.csv.zip')
df = pd.read_csv(df_zip.open('ratings.csv'))

df

userId  movieId  rating   timestamp
0              1      110     1.0  1425941529
1              1      147     4.5  1425942435
2              1      858     5.0  1425941523
3              1     1221     5.0  1425941546
4              1     1246     5.0  1425941556
...          ...      ...     ...         ...
26024284  270896    58559     5.0  1257031564
26024285  270896    60069     5.0  1257032032
26024286  270896    63082     4.5  1257031764
26024287  270896    64957     4.5  1257033990
26024288  270896    71878     2.0  1257031858

[26024289 rows x 4 columns]

*   **Taking 1/5 of the df**

In [214]:
end_row = int(len(df.index)*(1/5))


In [215]:
import pandas as pd
import numpy as np

#df = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/movie_ratings.csv') #load the csv file --> the "history table"

df = df[["userId", "movieId", "timestamp"]]
df = df.reset_index(drop = True)
df = df[:end_row]
df


userId  movieId   timestamp
0             1      110  1425941529
1             1      147  1425942435
2             1      858  1425941523
3             1     1221  1425941546
4             1     1246  1425941556
...         ...      ...         ...
5204852   53613     2354   995745432
5204853   53613     2378   995747472
5204854   53613     2384   995742106
5204855   53613     2387   995744604
5204856   53613     2394   995742969

[5204857 rows x 3 columns]

### **Rearranging the dataset**

*   **Sorting by timestamp [to account for order]**
(time: 21s)

In [216]:
df_grp = df.groupby('userId') #group by "userId"

df_grp_srt = df_grp.apply(lambda x: x.sort_values('timestamp')) #sorting each group by timestamp (ordered)

df_grp_srt

userId  movieId   timestamp
userId                                     
1      6             1     2762  1425941300
       13            1    54503  1425941313
       26            1   112552  1425941336
       23            1    96821  1425941382
       11            1     5577  1425941397
...                ...      ...         ...
53613  5204782   53613     1345   995748287
       5204756   53613      714   995752979
       5204824   53613     1923   995752979
       5204709   53613       47   995753014
       5204810   53613     1640   995753082

[5204857 rows x 3 columns]

In [217]:
#quick check on timestamp sorting:
df_grp_srt[df_grp_srt['userId'] == 99] #replace 99 with any number

userId  movieId  timestamp
userId                                 
99     9050      99        1  866605941
       9051      99       32  866605941
       9054      99      648  866605941
       9056      99      736  866605941
       9057      99      780  866605941
       9052      99      260  866605992
       9055      99      733  866605992
       9058      99      786  866605992
       9060      99     1073  866605992
       9053      99      376  866606030
       9059      99      802  866606031
       9061      99     1210  866606178

*   **Filtering out the timestamp column**
(time: 2s)

In [218]:
df_new = zip(df_grp_srt['userId'].tolist(),df_grp_srt['movieId'].tolist()) #put 'userId' and 'movieId' to list
df_new = pd.DataFrame(df_new)
df_new.columns = ['User IDs', 'Movie IDs'] #rename the columns
df_new.index.name = 'Index'

df_new

User IDs  Movie IDs
Index                       
0               1       2762
1               1      54503
2               1     112552
3               1      96821
4               1       5577
...           ...        ...
5204852     53613       1345
5204853     53613        714
5204854     53613       1923
5204855     53613         47
5204856     53613       1640

[5204857 rows x 2 columns]

------------------------------------------------------------------------------
*   **Step abandoned [crashed for trying to display entries in "user1 item1 item2 item3 ... itemN" format]**
------------------------------------------------------------------------------


In [ ]:
# aimed to arrange data in the format as such: "user1 item1 item2 item3 ... itemN" for all the rows
#it will crash --> don't run
#it will crash --> don't run
#it will crash --> don't run

df_new_wide = df_new.pivot_table(index='User IDs', columns='Index', values='Movie IDs', aggfunc='first') 

df_new_wide

*   **Rearranging the entries**

In [221]:
df_new1 = df_new.groupby('User IDs')['Movie IDs'].agg(list).reset_index() #take the "User ID" and "Movie ID" columns to create the users' history table
df_new1

User IDs                                          Movie IDs
0             1  [2762, 54503, 112552, 96821, 5577, 92439, 4878...
1             2  [780, 32, 648, 25, 141, 5, 786, 260, 1356, 788...
2             3  [3101, 527, 480, 500, 858, 1097, 1270, 1092, 4...
3             4  [4014, 4896, 1210, 1221, 415, 4084, 1097, 1431...
4             5  [1230, 157, 1302, 1270, 7, 3255, 3114, 3079, 3...
...         ...                                                ...
53608     53609         [1446, 1617, 1641, 1704, 1057, 1183, 1416]
53609     53610  [2468, 1210, 1617, 3093, 1940, 691, 2858, 3176...
53610     53611  [2001, 912, 785, 1597, 1961, 840, 765, 1755, 2...
53611     53612  [912, 898, 947, 597, 950, 1197, 2145, 2915, 29...
53612     53613  [1801, 2133, 1517, 2028, 1261, 2060, 858, 260,...

[53613 rows x 2 columns]

In [222]:
df_new2 = df_new1["Movie IDs"] #select "Movie ID" --> to creat pairs at the next stage
df_new2

0        [2762, 54503, 112552, 96821, 5577, 92439, 4878...
1        [780, 32, 648, 25, 141, 5, 786, 260, 1356, 788...
2        [3101, 527, 480, 500, 858, 1097, 1270, 1092, 4...
3        [4014, 4896, 1210, 1221, 415, 4084, 1097, 1431...
4        [1230, 157, 1302, 1270, 7, 3255, 3114, 3079, 3...
                               ...                        
53608           [1446, 1617, 1641, 1704, 1057, 1183, 1416]
53609    [2468, 1210, 1617, 3093, 1940, 691, 2858, 3176...
53610    [2001, 912, 785, 1597, 1961, 840, 765, 1755, 2...
53611    [912, 898, 947, 597, 950, 1197, 2145, 2915, 29...
53612    [1801, 2133, 1517, 2028, 1261, 2060, 858, 260,...
Name: Movie IDs, Length: 53613, dtype: object

*   **Finding all the pairs from the entries** (time: 10s + 3s)

In [223]:
from nltk import bigrams
bigrams_list = [list(bigrams(i)) for i in df_new2] #finding all the pairs
bigrams_list

bigrams_list = [[str(i) for i in sublist] for sublist in bigrams_list] #making all the pairs to string (for counting purposes)
bigrams_list

[['(2762, 54503)',
  '(54503, 112552)',
  '(112552, 96821)',
  '(96821, 5577)',
  '(5577, 92439)',
  '(92439, 4878)',
  '(4878, 68358)',
  '(68358, 59315)',
  '(59315, 858)',
  '(858, 110)',
  '(110, 1221)',
  '(1221, 1246)',
  '(1246, 2918)',
  '(2918, 2959)',
  '(2959, 99114)',
  '(99114, 33794)',
  '(33794, 58559)',
  '(58559, 81834)',
  '(81834, 69844)',
  '(69844, 1968)',
  '(1968, 4226)',
  '(4226, 147)',
  '(147, 91542)',
  '(91542, 98809)',
  '(98809, 91500)',
  '(91500, 73017)'],
 ['(780, 32)',
  '(32, 648)',
  '(648, 25)',
  '(25, 141)',
  '(141, 5)',
  '(5, 786)',
  '(786, 260)',
  '(260, 1356)',
  '(1356, 788)',
  '(788, 1210)',
  '(1210, 628)',
  '(628, 762)',
  '(762, 58)',
  '(58, 79)',
  '(79, 64)',
  '(64, 1233)',
  '(1233, 605)',
  '(605, 1552)',
  '(1552, 1475)',
  '(1475, 377)',
  '(377, 339)'],
 ['(3101, 527)',
  '(527, 480)',
  '(480, 500)',
  '(500, 858)',
  '(858, 1097)',
  '(1097, 1270)',
  '(1270, 1092)',
  '(1092, 4474)',
  '(4474, 1968)'],
 ['(4014, 4896)',


In [224]:
bigrams_list = [[i.replace('(', '').replace(')', '') for i in sublist] for sublist in bigrams_list] #remove all brackets
bigrams_list

[['2762, 54503',
  '54503, 112552',
  '112552, 96821',
  '96821, 5577',
  '5577, 92439',
  '92439, 4878',
  '4878, 68358',
  '68358, 59315',
  '59315, 858',
  '858, 110',
  '110, 1221',
  '1221, 1246',
  '1246, 2918',
  '2918, 2959',
  '2959, 99114',
  '99114, 33794',
  '33794, 58559',
  '58559, 81834',
  '81834, 69844',
  '69844, 1968',
  '1968, 4226',
  '4226, 147',
  '147, 91542',
  '91542, 98809',
  '98809, 91500',
  '91500, 73017'],
 ['780, 32',
  '32, 648',
  '648, 25',
  '25, 141',
  '141, 5',
  '5, 786',
  '786, 260',
  '260, 1356',
  '1356, 788',
  '788, 1210',
  '1210, 628',
  '628, 762',
  '762, 58',
  '58, 79',
  '79, 64',
  '64, 1233',
  '1233, 605',
  '605, 1552',
  '1552, 1475',
  '1475, 377',
  '377, 339'],
 ['3101, 527',
  '527, 480',
  '480, 500',
  '500, 858',
  '858, 1097',
  '1097, 1270',
  '1270, 1092',
  '1092, 4474',
  '4474, 1968'],
 ['4014, 4896',
  '4896, 1210',
  '1210, 1221',
  '1221, 415',
  '415, 4084',
  '4084, 1097',
  '1097, 1431',
  '1431, 2023',
  '2

*   **Counting all the pairs** (time: 3s)

In [225]:
from collections import Counter

all_pairs = [i for sublist in bigrams_list for i in sublist] #list of lists unpacked

pairs_counter = Counter(all_pairs) #counting unique pairs from "history" (i.e. ordered entries)
pairs_counter

Counter({'2762, 54503': 1,
         '54503, 112552': 2,
         '112552, 96821': 1,
         '96821, 5577': 1,
         '5577, 92439': 1,
         '92439, 4878': 1,
         '4878, 68358': 8,
         '68358, 59315': 79,
         '59315, 858': 10,
         '858, 110': 45,
         '110, 1221': 23,
         '1221, 1246': 8,
         '1246, 2918': 23,
         '2918, 2959': 34,
         '2959, 99114': 21,
         '99114, 33794': 10,
         '33794, 58559': 114,
         '58559, 81834': 4,
         '81834, 69844': 177,
         '69844, 1968': 3,
         '1968, 4226': 6,
         '4226, 147': 2,
         '147, 91542': 1,
         '91542, 98809': 8,
         '98809, 91500': 20,
         '91500, 73017': 9,
         '780, 32': 490,
         '32, 648': 226,
         '648, 25': 148,
         '25, 141': 68,
         '141, 5': 22,
         '5, 786': 64,
         '786, 260': 108,
         '260, 1356': 69,
         '1356, 788': 63,
         '788, 1210': 23,
         '1210, 628': 36,
         '6

### **Constructing a [blank] Covisitation Matrix**

*   **Unique IDs for labels**

In [226]:
unique_val = pd.DataFrame(pd.unique(df_new2.explode())) #unpack and collect unique values -> then make it a df
unique_val_srt = unique_val[0].sort_values().astype(str).tolist() #sorting df by unique values -> making them strings (for labeling purposes) in list
unique_val_srt

['1',
 '2',
 '3',
 '4',
 '5',
 '6',
 '7',
 '8',
 '9',
 '10',
 '11',
 '12',
 '13',
 '14',
 '15',
 '16',
 '17',
 '18',
 '19',
 '20',
 '21',
 '22',
 '23',
 '24',
 '25',
 '26',
 '27',
 '28',
 '29',
 '30',
 '31',
 '32',
 '33',
 '34',
 '35',
 '36',
 '37',
 '38',
 '39',
 '40',
 '41',
 '42',
 '43',
 '44',
 '45',
 '46',
 '47',
 '48',
 '49',
 '50',
 '51',
 '52',
 '53',
 '54',
 '55',
 '56',
 '57',
 '58',
 '59',
 '60',
 '61',
 '62',
 '63',
 '64',
 '65',
 '66',
 '67',
 '68',
 '69',
 '70',
 '71',
 '72',
 '73',
 '74',
 '75',
 '76',
 '77',
 '78',
 '79',
 '80',
 '81',
 '82',
 '83',
 '84',
 '85',
 '86',
 '87',
 '88',
 '89',
 '90',
 '92',
 '93',
 '94',
 '95',
 '96',
 '97',
 '98',
 '99',
 '100',
 '101',
 '102',
 '103',
 '104',
 '105',
 '106',
 '107',
 '108',
 '109',
 '110',
 '111',
 '112',
 '113',
 '114',
 '115',
 '116',
 '117',
 '118',
 '119',
 '120',
 '121',
 '122',
 '123',
 '124',
 '125',
 '126',
 '127',
 '128',
 '129',
 '130',
 '131',
 '132',
 '133',
 '134',
 '135',
 '136',
 '137',
 '138',
 '139',
 '1

*   **Blank matrix filled with zeros**

In [227]:
co_matrix = np.zeros((len(unique_val_srt), len(unique_val_srt)), dtype=int) #a blank covisitation matrix created
co_matrix = pd.DataFrame(co_matrix) #converting matrix to df
co_matrix.index = unique_val_srt #labeling the rows with unique IDs
co_matrix.columns = unique_val_srt #labeling the columns ...
co_matrix

1  2  3  4  5  6  7  8  9  10  ...  176185  176187  176189  176205  \
1       0  0  0  0  0  0  0  0  0   0  ...       0       0       0       0   
2       0  0  0  0  0  0  0  0  0   0  ...       0       0       0       0   
3       0  0  0  0  0  0  0  0  0   0  ...       0       0       0       0   
4       0  0  0  0  0  0  0  0  0   0  ...       0       0       0       0   
5       0  0  0  0  0  0  0  0  0   0  ...       0       0       0       0   
...    .. .. .. .. .. .. .. .. ..  ..  ...     ...     ...     ...     ...   
176211  0  0  0  0  0  0  0  0  0   0  ...       0       0       0       0   
176219  0  0  0  0  0  0  0  0  0   0  ...       0       0       0       0   
176239  0  0  0  0  0  0  0  0  0   0  ...       0       0       0       0   
176249  0  0  0  0  0  0  0  0  0   0  ...       0       0       0       0   
176271  0  0  0  0  0  0  0  0  0   0  ...       0       0       0       0   

        176207  176211  176219  176239  176249  176271  
1            0       0       0       0       0       0  
2            0       0       0       0       0       0  
3            0       0       0       0       0       0  
4            0       0       0       0       0       0  
5            0       0       0       0       0       0  
...        ...     ...     ...     ...     ...     ...  
176211       0       0       0       0       0       0  
176219       0       0       0       0       0       0  
176239       0       0       0       0       0       0  
176249       0       0       0       0       0       0  
176271       0       0       0       0       0       0  

[34920 rows x 34920 columns]

------------------------------------------------------------------------------
*   **Step abandoned [crashed for trying to display all the pairs in matrix]**
------------------------------------------------------------------------------


In [ ]:
#display all the pairs in the matrix
#don't run --> it will crash
#don't run --> it will crash
#don't run --> it will crash

for i in co_matrix.index: 
  for j in co_matrix.columns:
    co_matrix[i][j] = (str(i)+str(j))

co_matrix

### **Constructing the Covisitation Matrix** 
**Filling the Covisitation Matrix** (time: 2m36s)

In [228]:
for key, value in dict(pairs_counter).items():
   a = key.split(",")[0].strip()
   b = key.split(",")[1].split(":")[0].strip()
   c = value

   co_matrix.loc[a,b] = c ###### it may have writen c to cell [a, b], but it is not showing in the table below

co_matrix


1   2    3  4    5    6    7  8  9  10  ...  176185  176187  176189  \
1        0  22   10  8    9   22    6  0  3  74  ...       0       0       0   
2       18   0   10  3   10   17    3  4  1  17  ...       0       0       0   
3        4   4    0  9  311   84  131  2  4   2  ...       0       0       0   
4        0   2    5  0    9    0   10  0  0   2  ...       0       0       0   
5        3   7  153  2    0  171  154  2  6   8  ...       0       0       0   
...     ..  ..  ... ..  ...  ...  ... .. ..  ..  ...     ...     ...     ...   
176211   0   0    0  0    0    0    0  0  0   0  ...       0       0       0   
176219   0   0    0  0    0    0    0  0  0   0  ...       0       0       0   
176239   0   0    0  0    0    0    0  0  0   0  ...       0       0       0   
176249   0   0    0  0    0    0    0  0  0   0  ...       0       0       0   
176271   0   0    0  0    0    0    0  0  0   0  ...       0       0       0   

        176205  176207  176211  176219  176239  176249  176271  
1            0       0       0       0       0       0       0  
2            0       0       0       0       0       0       0  
3            0       0       0       0       0       0       0  
4            0       0       0       0       0       0       0  
5            0       0       0       0       0       0       0  
...        ...     ...     ...     ...     ...     ...     ...  
176211       0       0       0       0       0       0       0  
176219       0       0       0       0       0       0       0  
176239       0       0       0       0       0       0       0  
176249       0       0       0       0       0       0       0  
176271       0       0       0       0       0       0       0  

[34920 rows x 34920 columns]

In [ ]:
#for checking only (i.e. the top 50x50 matrix)
co_matrix[:50][:50]

In [ ]:
#for checking only (i.e. checking the values of a, b, c) 

for key, value in dict(pairs_counter).items():
   a = key.split(",")[0].strip()
   b = key.split(",")[1].split(":")[0].strip()
   c = value

   print (a, b, c)

### **Predicting**

*   **Normalizing the matrix (could be skipped)** (time: long)




In [ ]:
from sklearn.preprocessing import normalize #TO CONFIRM (How it should be normalized?) ALSO, cosine_similarity with or without the normalizing the matrix seem to give the same result

co_matrix_norm = normalize(co_matrix)
co_matrix_norm.index = unique_val_srt #label the rows with the list of unique item ID
co_matrix_norm.columns = unique_val_srt #label the columns ...

co_matrix_norm

*   **Cosine_similarity_scores (with normalized matrix)** (time: long)







In [ ]:
from sklearn.metrics.pairwise import cosine_similarity #[cosine_similarity (with normalized matrix)]

cos_score_df = pd.DataFrame(cosine_similarity(co_matrix_norm)) #compute similarity score with cosine_similarity (without normalized the matrix)
cos_score_df.index = unique_val_srt #label the rows with the list of unique item ID
cos_score_df.columns = unique_val_srt #label the columns ...

cos_score_df

In [229]:
new_user = np.zeros(len(co_matrix), dtype=int) #create a vector as a new user entry

for i in range(100): #generate 1 for 1000 random indices
  new_user[np.random.randint(0, len(co_matrix))]=1 

len(new_user) == len(co_matrix)
new_user

array([0, 0, 0, ..., 0, 0, 0])


*   **Predicting (making recommendations) for a new user**

In [231]:
A = new_user
B = co_matrix.to_numpy() #can use co_matrix directly here

out = np.matmul(A, B)
out_df = pd.DataFrame(zip(unique_val_srt, out, new_user), columns = ['Movie IDs','Scores', 'New User Entries']) #combine 'row labels', 'scores', 'new user entries' 
candidates = out_df.sort_values('Scores', ascending=False) #sorting by scores for top N candidates ('Entries' = 1 indicates user's 'implied preference')
candidates


Movie IDs  Scores  New User Entries
228         231     576                 0
589         595     485                 0
325         329     459                 0
315         318     436                 0
453         457     238                 0
...         ...     ...               ...
13903     70914       0                 0
13902     70912       0                 0
13901     70898       0                 0
13900     70891       0                 0
34919    176271       0                 0

[34920 rows x 3 columns]